In [2]:
import sys

import pandas
import scipy.io
import scipy.signal as sig
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import numpy as np
import pandas as pd
import os

import CinCDataset
import SAFERDataset

In [3]:
import importlib
importlib.reload(SAFERDataset)
importlib.reload(CinCDataset)

from DiagEnum import DiagEnum, feas1DiagToEnum

In [4]:
import matplotlib
matplotlib.rcParams["text.usetex"] = False

In [5]:
feas2_pt_data, feas2_ecg_data = SAFERDataset.load_feas_dataset(2, "dataframe")
feas2_ecg_data = feas2_ecg_data[feas2_ecg_data["length"] == 9120]

In [18]:
feas1_pt_data, feas1_ecg_data = SAFERDataset.load_feas_dataset(1, ecg_meas_diag=[d for d in DiagEnum if d != DiagEnum.Undecided])

        ptID   age         ptDiag     ptDiagRev1     ptDiagRev2  \
1409      17  76.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
1424      17  76.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
1425      17  76.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
1426      17  76.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
1435      17  76.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
...      ...   ...            ...            ...            ...   
162099  2134  68.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
162100  2134  68.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
162101  2134  68.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
162102  2134  68.0    DiagEnum.AF    DiagEnum.AF    DiagEnum.AF   
162441  2140  69.0  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.NoAF   

           ptDiagRev3  cardRev       measDiag        measDiagRev1  \
1409      DiagEnum.AF        1    DiagEnum.AF         DiagEnum.AF   
1424      DiagEnum.AF        1  DiagEnum.NoAF  DiagEnum.U

In [82]:
feas2_ecg_data = pd.read_pickle(r"C:\Users\daniel\Documents\2022_23_DSiromani\Feas2\ECGs\filtered_dataframe.pk")
feas2_pt_data = pd.read_csv(r"C:\Users\daniel\Documents\2022_23_DSiromani\Feas2\pt_data_anon.csv")
feas2_pt_data["ptID"] += 10000
feas2_ecg_data["ptID"] += 10000

feas1_ecg_data_clean = pd.read_pickle(r"C:\Users\daniel\Documents\2022_23_DSiromani\Feas1\ECGs\clean_ecg_dataset.pk")
feas1_pt_data = pd.read_csv(r"C:\Users\daniel\Documents\2022_23_DSiromani\Feas1\pt_data_anon.csv")
print(len(feas1_ecg_data_clean.index))

feas2_ecg_data_clean = pd.read_pickle(r"C:\Users\daniel\Documents\2022_23_DSiromani\Feas2\ECGs\clean_ecg_dataset.pk")
feas2_ecg_data_clean["ptID"] += 10000
print(len(feas2_ecg_data_clean.index))

all_clean_data = pd.concat([feas2_ecg_data_clean, feas1_ecg_data_clean], ignore_index=True)
all_clean_pt = pd.concat([feas2_pt_data[feas2_pt_data["ptID"].isin(feas2_ecg_data_clean["ptID"])], feas1_pt_data[feas1_pt_data["ptID"].isin(feas1_ecg_data_clean["ptID"])]])

all_clean_pt.set_index("ptID", drop=False, inplace=True)
all_clean_pt["noRecs"] = all_clean_data["ptID"].value_counts()
all_clean_pt["noHQrecs"] = all_clean_pt["noRecs"]
all_clean_pt.head()

2932
630


ptID   age  ptDiag  ptDiagRev1  ptDiagRev2  ptDiagRev3  cardRev  \
ptID                                                                      
10002  10002  79.0       3           6           3           6        1   
10005  10005  72.5       3           6           3           6        1   
10006  10006  79.0       3           6           3           6        1   
10011  10011  88.0       3           6           3           6        1   
10012  10012  70.5       3           6           3           6        1   

       noRecs  noHQrecs  noRecsPossAF  
ptID                                   
10002       1         1             4  
10005       3         3             5  
10006       2         2             2  
10011       1         1            28  
10012       9         9             7

In [6]:
from sklearn.model_selection import train_test_split

In [7]:
import torch.nn as nn
import torch

In [9]:
# Check cuda
print(torch.cuda.is_available())

True


In [8]:
class PCAAE_encoder(nn.Module):

    def __init__(self):
        super(PCAAE_encoder, self).__init__()

        self.conv_section1 = nn.Sequential(
            nn.Conv1d(1, 8, 19, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(8),
            nn.Conv1d(8, 8, 19, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(8)
        )

        self.conv_section2 = nn.Sequential(
            nn.Conv1d(8, 8, 19, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(8),
            nn.Conv1d(8, 8, 19, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(8)
        )

        self.conv_section3 = nn.Sequential(
            nn.Conv1d(8, 16, 9, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(16),
            nn.Conv1d(16, 16, 9, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(16)
        )

        self.conv_section4 = nn.Sequential(
            nn.Conv1d(16, 16, 9, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(16),
            nn.Conv1d(16, 16, 9, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(16)
        )

        self.conv_section5 = nn.Sequential(
            nn.Conv1d(16, 32, 7, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(32),
            nn.Conv1d(32, 32, 7, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(32)
        )

        """
        self.conv_section6 = nn.Sequential(
            nn.Conv1d(64, 64, 19, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(64),
            nn.Conv1d(64, 64, 19, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(64)
        )
        """

        self.conv_section7 = nn.Sequential(
            nn.Conv1d(32, 32, 7, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(32),
            nn.Conv1d(32, 32, 7, padding='same'),
            nn.ReLU(),
            nn.BatchNorm1d(32)
        )

        self.encoder_linear = nn.Linear(2048, 2)

    def forward(self, x):
        # [1, 2048]
        x = self.conv_section1(x)
        x = nn.functional.max_pool1d(x, 2)

        # [16, 1024]
        x = self.conv_section2(x) + x
        x = nn.functional.max_pool1d(x, 2)

        # [32, 512]
        x = self.conv_section3(x)
        x = nn.functional.max_pool1d(x, 2)

        # [32, 256]
        x = self.conv_section4(x) + x
        x = nn.functional.max_pool1d(x, 2)

        # [64, 128]
        x = self.conv_section5(x)
        x = nn.functional.max_pool1d(x, 2)

        # [64, 64]
        # x = self.conv_section6(x)

        # [64, 64]
        x = self.conv_section7(x)

        # [80, 64]
        x = torch.flatten(x, -2)

        # [5120]
        x = self.encoder_linear(x)

        return x



class PCAAE_decoder(nn.Module):

    def __init__(self, z_dim):
        super(PCAAE_decoder, self).__init__()

        self.decoder_linear = nn.Linear(z_dim, 2048)
        self.decoder_batchnorm = nn.BatchNorm1d(2048)

        self.transconv_section1 = nn.Sequential(
            nn.ConvTranspose1d(8, 1, 19, padding=9, stride=1),
        )

        self.transconv_section2 = nn.Sequential(
            nn.ConvTranspose1d(16, 8, 20, padding=9, stride=2),
            nn.ReLU(),
            nn.BatchNorm1d(8),
        )

        self.transconv_section3 = nn.Sequential(
            nn.ConvTranspose1d(16, 16, 20, padding=9, stride=2),
            nn.ReLU(),
            nn.BatchNorm1d(16),
        )

        self.transconv_section4 = nn.Sequential(
            nn.ConvTranspose1d(16, 16, 10, padding=4, stride=2),
            nn.ReLU(),
            nn.BatchNorm1d(16),
        )

        self.transconv_section5 = nn.Sequential(
            nn.ConvTranspose1d(32, 16, 10, padding=4, stride=2),
            nn.ReLU(),
            nn.BatchNorm1d(16),
        )

        self.transconv_section6 = nn.Sequential(
            nn.ConvTranspose1d(32, 32, 8, padding=3, stride=2),
            nn.ReLU(),
            nn.BatchNorm1d(32)
        )

        self.transconv_section7 = nn.Sequential(
            nn.ConvTranspose1d(32, 32, 7, padding=3, stride=1),
            nn.ReLU(),
            nn.BatchNorm1d(32)
        )

    def forward(self, z):

        z = self.decoder_linear(z)
        z = torch.nn.functional.relu(z)
        z = self.decoder_batchnorm(z)

        # [5120]
        z = torch.reshape(z, (-1, 32, 64))
        # [80, 64]
        z = self.transconv_section7(z)
        # print(z.shape)
        # [64, 64]
        z = self.transconv_section6(z)
        # print(z.shape)
        # [64, 64]
        z = self.transconv_section5(z)
        # print(z.shape)
        # [64, 128]
        z = self.transconv_section4(z)
        # print(z.shape)
        # [48, 256]
        z = self.transconv_section3(z)
        # print(z.shape)
        # [32, 512]
        z = self.transconv_section2(z)
        # print(z.shape)
        # [16, 1024]
        z = self.transconv_section1(z)
        # print(z.shape)
        # [1, 2048]
        return z

In [11]:
# Onehot encoding
from torch.utils.data import Dataset, DataLoader

def generate_onehot(c):
    if c == "N":
        return np.array([1, 0, 0, 0])
    if c == "O":
        return np.array([0, 1, 0, 0])
    if c == "A":
        return np.array([0, 0, 1, 0])
    if c == "~":
        return np.array([0, 0, 0, 1])

def generate_index(c):
    if c == "N":
        return 0
    if c == "O":
        return 0
    if c == "A":
        return 0
    if c == "~":
        return 1

# dataset["onehot"] = dataset["class"].map(generate_onehot)
# dataset["class_index"] = dataset["class"].map(generate_index)

class Dataset(torch.utils.data.Dataset):
  'Characterizes a dataset for PyTorch'
  def __init__(self, dataset):
        'Initialization'
        self.dataset = dataset

  def __len__(self):
        'Denotes the total number of samples'
        return len(self.dataset.index)

  def __getitem__(self, index):
        'Generates one sample of data'
        # Select sample
        row = self.dataset.iloc[index]

        X = row["data"]
        y = row["class_index"]
        ind = row.name

        return X, y, ind

In [12]:
def split_to_segments(dataset, new_len, orig_len, overlap=0):
    sections = []

    step = int(round(new_len * (1 - overlap)))
    num_sections = (orig_len - (new_len - step)) // step
    for _, series in dataset.iterrows():
        for i in range(num_sections):
            section_series = series.copy()
            section_series["data"] = section_series["data"][i*step: i*step + new_len]
            section_series["rec_ind"] = series.name
            section_series["rec_pos"] = i
            # Keep all other data (ptid, measDiag etc the same for each section as the source ECG)
            sections.append(section_series)

    return pd.DataFrame(sections).reset_index()

In [13]:
# For CinC data

train_dataset, test_dataset = train_test_split(dataset, test_size=0.15, stratify=dataset["class_index"])

# Normalise the data
train_dataset["data"] = (train_dataset["data"] - train_dataset["data"].map(lambda x: x.mean()))/train_dataset["data"].map(lambda x: x.std())
test_dataset["data"] = (test_dataset["data"] - test_dataset["data"].map(lambda x: x.mean()))/test_dataset["data"].map(lambda x: x.std())

print(train_dataset["data"].map(lambda x: x.mean()))
print(train_dataset["data"].map(lambda x: x.std()))

torch_dataset_train = Dataset(split_to_segments(train_dataset[train_dataset["class_index"] == 0], 2048, 9000, 0))
torch_dataset_test = Dataset(split_to_segments(test_dataset[test_dataset["class_index"] == 0], 2048, 9000, 0))

train_dataloader = DataLoader(torch_dataset_train, batch_size=32, shuffle=True, pin_memory=True)
test_dataloader = DataLoader(torch_dataset_test, batch_size=32, shuffle=True, pin_memory=True)

A00491    9.473903e-18
A08427    1.657933e-17
A00738    0.000000e+00
A07861   -2.052679e-17
A03273   -1.815831e-17
              ...     
A05015   -1.342136e-17
A02962    9.868649e-18
A07163   -2.447425e-17
A00448    1.421085e-17
A00570   -1.736882e-17
Name: data, Length: 5080, dtype: float64
A00491    1.0
A08427    1.0
A00738    1.0
A07861    1.0
A03273    1.0
         ... 
A05015    1.0
A02962    1.0
A07163    1.0
A00448    1.0
A00570    1.0
Name: data, Length: 5080, dtype: float64


In [13]:
# For SAFER data
# Split train and test data according to each patient
def make_SAFER_dataloaders(pt_data, ecg_data, test_frac, only_clean_training=True):
    pt_data["noLQrecs"] = pt_data["noRecs"] - pt_data["noHQrecs"]  # for Feas1 this might include stuff flagged by zenicor as noisy?
    train_patients = []
    test_patients = []

    for val, df in pt_data.groupby("noLQrecs"):
        print(f"processing {val}")
        print(f"number of patients {len(df.index)}")
        test = df.sample(frac=test_frac)
        test_patients.append(test)
        train_patients.append(df[~df["ptID"].isin(test["ptID"])])

    train_pt_df = pd.concat(train_patients)
    test_pt_df = pd.concat(test_patients)

    print(f"Test high quality: {test_pt_df['noHQrecs'].sum()} low quality: {test_pt_df['noLQrecs'].sum()} ")
    print(f"Train high quality: {train_pt_df['noHQrecs'].sum()} low quality: {train_pt_df['noLQrecs'].sum()} ")

    train_dataloader = None
    test_dataloader = None

    train_dataset = None
    test_dataset = None

    if not train_pt_df.empty:
        # get ECG datasets
        train_dataset = split_to_segments(ecg_data[ecg_data["ptID"].isin(train_pt_df["ptID"])], 2048, 9120, 0.5)
        # Normalise
        train_dataset["data"] = (train_dataset["data"] - train_dataset["data"].map(lambda x: x.mean()))/train_dataset["data"].map(lambda x: x.std())

        if only_clean_training:
            torch_dataset_train = Dataset(train_dataset[train_dataset["class_index"] == 0])
        else:
            torch_dataset_train = Dataset(train_dataset)

        train_dataloader = DataLoader(torch_dataset_train, batch_size=64, shuffle=True, pin_memory=True)

    if not test_pt_df.empty:
        test_dataset = split_to_segments(ecg_data[ecg_data["ptID"].isin(test_pt_df["ptID"])], 2048, 9120, 0.5)
        test_dataset["data"] = (test_dataset["data"] - test_dataset["data"].map(lambda x: x.mean()))/test_dataset["data"].map(lambda x: x.std())
        torch_dataset_test = Dataset(test_dataset)
        test_dataloader = DataLoader(torch_dataset_test, batch_size=64, shuffle=True, pin_memory=True)

    return train_dataloader, test_dataloader, train_dataset, test_dataset

# train_dataloader, _ = make_SAFER_dataloaders(feas1_pt_data, feas1_ecg_data, test_frac=0)
train_dataloader, test_dataloader, train_dataset, test_dataset = make_SAFER_dataloaders(feas2_pt_data, feas2_ecg_data, test_frac=0.2, only_clean_training=False)

processing 0
number of patients 165
processing 1
number of patients 43
processing 2
number of patients 19
processing 3
number of patients 13
processing 4
number of patients 9
processing 5
number of patients 5
processing 6
number of patients 8
processing 7
number of patients 3
processing 8
number of patients 3
processing 9
number of patients 1
processing 10
number of patients 3
processing 11
number of patients 1
processing 12
number of patients 4
processing 13
number of patients 3
processing 14
number of patients 1
processing 15
number of patients 1
processing 16
number of patients 1
processing 17
number of patients 1
processing 21
number of patients 1
processing 26
number of patients 1
processing 27
number of patients 1
processing 33
number of patients 1
Test high quality: 4661 low quality: 101 
Train high quality: 18018 low quality: 479 


In [57]:
feas2_ecg_data["measDiag"].value_counts()

DiagEnum.Undecided                 22018
DiagEnum.NoAF                        758
DiagEnum.PoorQuality                 465
DiagEnum.AF                           16
DiagEnum.CannotExcludePathology        2
Name: measDiag, dtype: int64

In [104]:
_, noisy_test_dataloader, _, noisy_test_dataset = make_SAFER_dataloaders(feas2_pt_data, feas2_ecg_data[~feas2_ecg_data["measID"].isin(train_dataset)], test_frac=1, only_clean_training=False)

processing 0
number of patients 165
processing 1
number of patients 43
processing 2
number of patients 19
processing 3
number of patients 13
processing 4
number of patients 9
processing 5
number of patients 5
processing 6
number of patients 8
processing 7
number of patients 3
processing 8
number of patients 3
processing 9
number of patients 1
processing 10
number of patients 3
processing 11
number of patients 1
processing 12
number of patients 4
processing 13
number of patients 3
processing 14
number of patients 1
processing 15
number of patients 1
processing 16
number of patients 1
processing 17
number of patients 1
processing 21
number of patients 1
processing 26
number of patients 1
processing 27
number of patients 1
processing 33
number of patients 1
Test high quality: 22679 low quality: 580 
Train high quality: 0 low quality: 0 


In [111]:
noisy_test_dataset["measDiag"].value_counts()

DiagEnum.Undecided                 154126
DiagEnum.NoAF                        5306
DiagEnum.PoorQuality                 3255
DiagEnum.AF                           112
DiagEnum.CannotExcludePathology        14
Name: measDiag, dtype: int64

In [89]:
train_dataloader, test_dataloader, train_dataset, test_dataset = make_SAFER_dataloaders(all_clean_pt, all_clean_data, test_frac=0.2, only_clean_training=False)

processing 0
number of patients 275
Test high quality: 576 low quality: 0 
Train high quality: 2986 low quality: 0 


In [58]:
train_dataset["class_index"].value_counts()

0    97811
1     2107
Name: class_index, dtype: int64

In [1]:
# Use as a denoising autoencoder with the MIT BIH database

pk_path = "mit-bih-noise-stress-test-database/database.pk"
nst_df = pd.load_pickle(pk_path)

NameError: name 'pd' is not defined

In [ ]:
# dataset["onehot"] = dataset["class"].map(generate_onehot)
nst_df["class_index"] = nst_df["class"].map(generate_index)

class NSTDataset(torch.utils.data.Dataset):
  'Characterizes a dataset for PyTorch'
  def __init__(self, dataset):
        'Initialization'
        self.dataset = dataset

  def __len__(self):
        'Denotes the total number of samples'
        return len(self.dataset.index)

  def __getitem__(self, index):
        'Generates one sample of data'
        # Select sample
        row = self.dataset.iloc[index]

        X = row["data"]  # The only dataset and nst dataset difference is in this line!
        y = row["class_index"]

        return X, y

# Normalise the data
nst_df["data"] = (nst_df["data"] - nst_df["data"].map(lambda x: x.mean()))/nst_df["data"].map(lambda x: x.std())

torch_dataset_nst = NSTDataset(nst_df)
nst_dataloader = DataLoader(torch_dataset_nst, batch_size=32, shuffle=True, pin_memory=True)

In [ ]:
# For feas1 data its too big to load into ram so we make dataloaders as we need them
import math

chunk_size = 20000
num_chunks = math.ceil(162515 / chunk_size )

print(num_chunks)

for i in range(num_chunks):
    print([chunk_size * i, chunk_size * (i + 1)])
    SAFERDataset.load_feas_dataset(feas=1, save_name=f"dataframe_{i}.pk", ecg_range=[chunk_size * i, chunk_size * (i + 1)])

In [63]:
import math

chunk_size = 20000
num_chunks = math.ceil(162515 / chunk_size )

def get_feas1_dataloader(chunk_num):
    feas1_pt_data, feas1_ecg_data = SAFERDataset.load_feas_dataset(1, f"dataframe_{chunk_num}.pk", ecg_range=[chunk_size * chunk_num, chunk_size * (chunk_num + 1)])
    train_dataset = split_to_segments(feas1_ecg_data, 2048, 9120, 0.5)
    train_dataset["data"] = (train_dataset["data"] - train_dataset["data"].map(lambda x: x.mean()))/train_dataset["data"].map(lambda x: x.std())

    torch_dataset_train = Dataset(train_dataset)
    train_dataloader = DataLoader(torch_dataset_train, batch_size=128, shuffle=True, pin_memory=True)

    return train_dataloader

In [31]:
num_epochs = 10

if torch.cuda.is_available():
    print("Using Cuda")
    device = torch.device("cuda")
else:
    print("Using CPU")
    device = torch.device("cpu")

z_dim = 1
end_z_dim = 3

encoders = []


# Use weightings to avoid

# class_counts = torch.tensor(dataset["class_index"].value_counts().values.astype(np.float32))
# class_weights = torch.nn.functional.normalize(1.0/class_counts, dim=0)
def kl_latent_loss(means, stds):
    vars = stds ** 2
    return 1/500 * torch.mean( - torch.log(vars) + vars + means ** 2 - 1)

mse_loss = torch.nn.MSELoss()
loss_func = lambda x, s, z_mean, z_std: kl_latent_loss(z_mean, z_std) +  mse_loss(x, s)

num_batches = len(train_dataloader)
num_test_batches = len(test_dataloader)

Using Cuda


In [16]:
z = torch.unsqueeze(torch.concat([torch.ones(60), torch.ones(60)*0.1], axis=0), dim=0)
print(z)
kl_latent_loss(z)

tensor([[1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000,
         1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000,
         1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000,
         1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000,
         1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000,
         1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000,
         1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 0.1000, 0.1000, 0.1000,
         0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000,
         0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000,
         0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000,
         0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000,
         0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000, 0.1000,
         0.1000, 0.1000, 0.1

tensor(0.0462)

In [64]:
# # Train on feas 1 as well!

model = model.to(device)
import copy

best_test_loss = 100
best_model = copy.deepcopy(model).cpu()

for epoch in range(num_epochs):
    total_loss = 0
    print(f"starting epoch {epoch} ...")
    # Train
    model.train()

    for ds_ind in range(num_chunks + 1):
        print(f"training on dataset: {ds_ind}")
        if ds_ind == 0:
            train_dataloader_part = train_dataloader
        else:
            train_dataloader_part = get_feas1_dataloader(ds_ind-1)

        for i, (signals, _, _) in enumerate(train_dataloader_part):
            signals = torch.unsqueeze(signals.to(device), 1).float()
            # fft = torch.abs(torch.fft.fft(signals))
            # signals = torch.cat([signals, fft], dim=1)
            # labels = labels.type(torch.LongTensor)
            optimizer.zero_grad()
            output, latents = model(signals)
            loss = loss_func(output, signals, latents)
            # print(kl_latent_loss(latents), loss)
            # print(loss)
            loss.backward()

            nn.utils.clip_grad_norm_(model.parameters(), max_norm=2.0, norm_type=2)

            optimizer.step()
            total_loss += float(loss)

        print(f"Total loss {total_loss/num_batches}")

    print(f"Epoch {epoch} finished with average loss {total_loss/num_batches}")
    print("Testing ...")
    # Test
    test_loss = 0
    with torch.no_grad():
        model.eval()
        for i, (signals, _, _)in enumerate(test_dataloader):
            signals = torch.unsqueeze(signals.to(device), 1).float()
            # fft = torch.abs(torch.fft.fft(signals))
            # signals = torch.cat([signals, fft], dim=1)
            # labels = labels.type(torch.LongTensor)

            output, latents = model (signals)
            loss = loss_func(output, signals, latents)
            test_loss += float(loss)

    print(f"Average test loss: {test_loss/num_test_batches}")

    if test_loss/num_test_batches < best_test_loss:
        best_model = copy.deepcopy(model).cpu()
        best_test_loss = test_loss/num_test_batches

model = best_model

starting epoch 0 ...
training on dataset: 0
Total loss 1.0663332126357339
training on dataset: 1
Total loss 1.6060867816705862
training on dataset: 2
Total loss 1.878825947890361
training on dataset: 3
Total loss 2.0822258379868446
training on dataset: 4
Total loss 2.267167119931778
training on dataset: 5
Total loss 2.4346330501282263
training on dataset: 6
Total loss 2.584265530786731
training on dataset: 7
Total loss 2.7291548616907506
training on dataset: 8
Total loss 2.8796171174693503
training on dataset: 9
Total loss 2.898401502095325
Epoch 0 finished with average loss 2.898401502095325
Testing ...
Average test loss: 0.19433820077870895
starting epoch 1 ...
training on dataset: 0
Total loss 0.23145795761394133
training on dataset: 1
Total loss 0.368062896503758
training on dataset: 2
Total loss 0.5091250058211071
training on dataset: 3
Total loss 0.6435096615808569
training on dataset: 4
Total loss 0.7757014828267842
training on dataset: 5
Total loss 0.9077038242840584
training o

KeyboardInterrupt: 

In [37]:
import copy

encoders = []

for z_dim in range(1, end_z_dim+1):
    best_test_loss = 100

    encoders.append(PCAAE_encoder().to(device))
    encode_optimizer = torch.optim.SGD(encoders[-1].parameters(), lr=0.1, momentum=0.8)

    decoder = PCAAE_decoder(z_dim=1).to(device)
    decode_optimizer = torch.optim.SGD(decoder.parameters(), lr=0.1, momentum=0.8)

    best_encoder = copy.deepcopy(encoders[-1]).cpu()
    best_decoder = copy.deepcopy(decoder).cpu()

    print(f"starting with {z_dim} latent dimension")

    for epoch in range(num_epochs):
        total_loss = 0
        print(f"starting epoch {epoch} ...")
        # Train
        encoders[-1].train()
        decoder.train()
        for i, (signals, _, _) in enumerate(train_dataloader):
            signals = torch.unsqueeze(signals.to(device), 1).float()
            # fft = torch.abs(torch.fft.fft(signals))
            # signals = torch.cat([signals, fft], dim=1)
            # labels = labels.type(torch.LongTensor)
            decode_optimizer.zero_grad()
            encode_optimizer.zero_grad()

            z_mean = []
            z_var = []
            for encoder in encoders:
                l = encoder(signals)
                z_mean.append(l[:, 0])
                z_var.append(l[:, 1])

            z_mean = torch.concat(z_mean, dim=0)
            z_var = torch.concat(z_var, dim=0)

            # sample
            z = torch.randn(z_dim).to(device) * z_var.to(device) + z_mean.to(device)
            z = torch.unsqueeze(z, dim=1)
            output = decoder(z)

            loss = loss_func(output, signals, z_mean, z_var)
            loss.backward()

            nn.utils.clip_grad_norm_(encoders[-1].parameters(), max_norm=2.0, norm_type=2)
            nn.utils.clip_grad_norm_(decoder.parameters(), max_norm=2.0, norm_type=2)

            encode_optimizer.step()
            decode_optimizer.step()
            total_loss += float(loss)

        print(f"Epoch {epoch} finished with average loss {total_loss/num_batches}")
        print("Testing ...")
        # Test
        test_loss = 0
        with torch.no_grad():
            encoders[-1].eval()
            decoder.eval()
            for i, (signals, _, _)in enumerate(test_dataloader):
                signals = torch.unsqueeze(signals.to(device), 1).float()
                # fft = torch.abs(torch.fft.fft(signals))
                # signals = torch.cat([signals, fft], dim=1)
                # labels = labels.type(torch.LongTensor)

                decode_optimizer.zero_grad()
                encode_optimizer.zero_grad()

                z_mean = []
                z_var = []
                for encoder in encoders:
                    l = encoder(signals)
                    z_mean.append(l[:, 0])
                    z_var.append(l[:, 1])

                z_mean = torch.concat(z_mean, dim=0)
                z_var = torch.concat(z_var, dim=0)

                # sample
                z = torch.randn(z_dim).to(device) * z_var.to(device) + z_mean.to(device)
                z = torch.unsqueeze(z, dim=1)
                output = decoder(z)

                loss = loss_func(output, signals, z_mean, z_var)
                test_loss += float(loss)

        print(f"Average test loss: {test_loss/num_test_batches}")

        if test_loss/num_test_batches < best_test_loss:
            best_encoder = copy.deepcopy(encoders[-1]).cpu()
            best_decoder = copy.deepcopy(decoder).cpu()
            best_test_loss = test_loss/num_test_batches

    encoders[-1] = best_encoder.to(device)

model = best_model

starting with 1 latent dimension
starting epoch 0 ...
Epoch 0 finished with average loss 1.0160466583349959
Testing ...
Average test loss: 1.0227606245057368
starting epoch 1 ...
Epoch 1 finished with average loss 0.9767999288003907
Testing ...
Average test loss: 1.1512726379447615
starting epoch 2 ...
Epoch 2 finished with average loss 0.9747424552975436
Testing ...
Average test loss: 1.1570136035701364
starting epoch 3 ...
Epoch 3 finished with average loss 0.974041797161809
Testing ...
Average test loss: 1.177915806962524
starting epoch 4 ...
Epoch 4 finished with average loss 0.9731178111709625
Testing ...
Average test loss: 1.1578223008569508
starting epoch 5 ...
Epoch 5 finished with average loss 0.9726009026994347
Testing ...
Average test loss: 1.2188991315076538
starting epoch 6 ...
Epoch 6 finished with average loss 0.9721862168415732
Testing ...
Average test loss: 1.0530461888624474
starting epoch 7 ...
Epoch 7 finished with average loss 0.9719069091522176
Testing ...
Average

RuntimeError: The size of tensor a (2) must match the size of tensor b (128) at non-singleton dimension 0

In [95]:
model_save = copy.deepcopy(model).cpu()

In [97]:
model = model.to(device)

In [65]:
model = best_model.to(device)

In [66]:
# Save a model
torch.save(model.state_dict(), "TrainedModels/Autoencoder_new_6_epochs_all_feas1_feas2.pt")
train_dataset.to_pickle("TrainedModels/Autoencoder_new_6_epochs_all_feas1_feas2_train_set.pk")

In [15]:
model = CVAE().to(device)
model.load_state_dict(torch.load("TrainedModels/Autoencoder_new_6_epochs_all_feas1_feas2.pt", map_location=device))

<All keys matched successfully>

In [20]:
# Reload the training and dataset with the model so we dont test on stuff we trained on
train_dataset = pd.read_pickle("TrainedModels/Autoencoder_new_6_epochs_all_feas1_feas2_train_set.pk")

train_dataset["data"] = (train_dataset["data"] - train_dataset["data"].map(lambda x: x.mean()))/train_dataset["data"].map(lambda x: x.std())
torch_dataset_train = Dataset(train_dataset)
train_dataloader = DataLoader(torch_dataset_train, batch_size=32, shuffle=True, pin_memory=True)

test_pt_df = feas2_pt_data[~feas2_pt_data["ptID"].isin(train_dataset["ptID"])]

if not test_pt_df.empty:
    test_dataset = test_dataset[test_dataset["measDiag"] != DiagEnum.Undecided]
    test_dataset = split_to_segments(feas2_ecg_data[feas2_ecg_data["ptID"].isin(test_pt_df["ptID"])], 2048, 9120, 0.5)
    test_dataset["data"] = (test_dataset["data"] - test_dataset["data"].map(lambda x: x.mean()))/test_dataset["data"].map(lambda x: x.std())
    torch_dataset_test = Dataset(test_dataset)
    test_dataloader = DataLoader(torch_dataset_test, batch_size=32, shuffle=True, pin_memory=True)

### Reconstruction for clean samples

In [17]:
print(len(train_dataset.index))

129353


In [21]:
# Plot test data reconstruction
test_dataset["reconstruction"] = None

with torch.no_grad():
    model.eval()
    for i, (signals, _, ind) in enumerate(test_dataloader):
        signals = torch.unsqueeze(signals.to(device), 1).float()
        # fft = torch.abs(torch.fft.fft(signals))
        # signals = torch.cat([signals, fft], dim=1)
        # labels = labels.type(torch.LongTensor)

        output, latents  = model(signals)
        # print(latents)
        output = output.detach().cpu().numpy()
        signals_np = signals.detach().cpu().numpy()

        for i, o in zip(ind, output[:, 0, :]):
            test_dataset["reconstruction"].loc[int(i)] = o

test_df = test_dataset.dropna(subset=["reconstruction"])

C:\Users\daniel\AppData\Local\Temp\ipykernel_71904\3627126355.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_dataset["reconstruction"].loc[int(i)] = o


In [32]:
test_df = test_dataset.dropna(subset=["reconstruction"])

In [22]:
test_df["measDiag"].value_counts()

DiagEnum.Undecided                 58793
DiagEnum.NoAF                       2884
DiagEnum.PoorQuality                1148
DiagEnum.AF                           56
DiagEnum.CannotExcludePathology       14
Name: measDiag, dtype: int64

In [25]:
from matplotlib.ticker import AutoMinorLocator
import matplotlib
matplotlib.use('TkAgg')

def plot_ecg_and_reconstruction(x, r, fs=300, n_split=3):
    sample_len = x.shape[0]
    time_axis = np.arange(sample_len)/fs

    cuts = np.round(np.linspace(0, sample_len-1, n_split+1)).astype(int)

    fig, ax = plt.subplots(n_split, 1, figsize=(16, 10), squeeze=False)
    for j in range(n_split):
        ax[j][0].plot(time_axis[cuts[j]:cuts[j+1]], x[cuts[j]:cuts[j+1]])
        ax[j][0].plot(time_axis[cuts[j]:cuts[j+1]], r[cuts[j]:cuts[j+1]])
        ax[j][0].set_xlabel("Time")
        ax[j][0].set_xlim((time_axis[cuts[j]], time_axis[cuts[j+1]]))

        t_s = time_axis[cuts[j]]
        t_f = time_axis[cuts[j+1]]
        time_ticks = np.arange(t_s - t_s%0.2, t_f + (0.2 - t_f%0.2), 0.2)
        decimal_labels = ~np.isclose(time_ticks, np.round(time_ticks))
        time_labels = np.round(time_ticks).astype(int).astype(str)
        time_labels[decimal_labels] = ""

        ax[j][0].set_xticks(time_ticks, time_labels)

        ax[j][0].xaxis.set_major_formatter(plt.NullFormatter())
        ax[j][0].yaxis.set_major_formatter(plt.NullFormatter())

        ax[j][0].xaxis.set_minor_locator(AutoMinorLocator(5))
        ax[j][0].yaxis.set_minor_locator(AutoMinorLocator(5))

        ax[j][0].grid(which='major', linestyle='-', linewidth='0.5', color='black')
        ax[j][0].grid(which='minor', linestyle='-', linewidth='0.5', color='lightgray')

    plt.show()

for _, ecg in test_df[test_df["measDiag"] == DiagEnum.PoorQuality].iterrows():
    # print(ecg)
    print(ecg[["ptDiag", "measDiag", "tag_orig_Poor_Quality", "poss_AF_tag"]])
    plot_ecg_and_reconstruction(ecg["data"], ecg["reconstruction"], n_split=1)

ptDiag                          DiagEnum.NoAF
measDiag                 DiagEnum.PoorQuality
tag_orig_Poor_Quality                       0
poss_AF_tag                                 1
Name: 1225, dtype: object
ptDiag                          DiagEnum.NoAF
measDiag                 DiagEnum.PoorQuality
tag_orig_Poor_Quality                       0
poss_AF_tag                                 1
Name: 1226, dtype: object
ptDiag                          DiagEnum.NoAF
measDiag                 DiagEnum.PoorQuality
tag_orig_Poor_Quality                       0
poss_AF_tag                                 1
Name: 1227, dtype: object
ptDiag                          DiagEnum.NoAF
measDiag                 DiagEnum.PoorQuality
tag_orig_Poor_Quality                       0
poss_AF_tag                                 1
Name: 1228, dtype: object
ptDiag                          DiagEnum.NoAF
measDiag                 DiagEnum.PoorQuality
tag_orig_Poor_Quality                       0
poss_AF_tag           

KeyboardInterrupt: 

In [62]:
def plot_ecg_and_reconstruction_for_classes(xs, rs, titles, fs=300):
    fig, ax = plt.subplots(len(xs), 1, figsize=(6, 7))

    for j, (x, r, t) in enumerate(zip(xs, rs, titles)):
        sample_len = x.shape[0]
        time_axis = np.arange(sample_len)/fs

        ax[j].plot(time_axis, x)
        ax[j].plot(time_axis, r)
        ax[j].set_xlabel("Time")
        ax[j].set_xlim((time_axis[0], time_axis[-1]))

        ax[j].set_xticks(np.arange(time_axis[0], time_axis[-1]+0.2,0.2))
        ax[j].set_title(t)

        ax[j].xaxis.set_major_formatter(plt.NullFormatter())
        ax[j].yaxis.set_major_formatter(plt.NullFormatter())

        ax[j].xaxis.set_minor_locator(AutoMinorLocator(5))
        ax[j].yaxis.set_minor_locator(AutoMinorLocator(5))

        ax[j].grid(which='major', linestyle='-', linewidth='0.5', color='black')
        ax[j].grid(which='minor', linestyle='-', linewidth='0.5', color='lightgray')

    fig.tight_layout()
    # plt.show()
    plt.savefig("TMRFigures/cvae_reconst_examples_large_dataset.png")

ecg_ind_list = [3195, 2916, 1563, 1561]  # 2192 # 441 # 315

xs = test_df.loc[ecg_ind_list]["data"].tolist()
rs = test_df.loc[ecg_ind_list]["reconstruction"].tolist()
titles = test_df.loc[ecg_ind_list].apply(lambda x: f"{x['measDiag'].name} e = {x['r_err']:.3f}", axis=1)   # ["measDiag"].map(lambda x: x.name).tolist()
print(len(titles))

plot_ecg_and_reconstruction_for_classes(xs, rs, titles)

4


### Reconstruction for noisy samples

In [26]:
# Try on some noisy samples

noisy_dataset = Dataset(test_dataset[test_dataset["class_index"] == 1])
noisy_dataloader = DataLoader(noisy_dataset, batch_size=32, shuffle=True, pin_memory=True)

with torch.no_grad():
    model.eval()
    for i, (signals, _, _) in enumerate(test_dataloader):
        signals = torch.unsqueeze(signals.to(device), 1).float()
        # fft = torch.abs(torch.fft.fft(signals))
        # signals = torch.cat([signals, fft], dim=1)
        # labels = labels.type(torch.LongTensor)

        output= model(signals)[0].detach().cpu().numpy()
        signals_np = signals.detach().cpu().numpy()

        break

In [20]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

num_rows = 8
num_cols = 4

num_class_samples = num_cols * num_rows
fig = make_subplots(rows=num_rows, cols=num_cols)

for i, (reconstruction, sample) in enumerate(zip(output, signals_np)):
    fig.add_trace(go.Scatter(y=sample, marker_line_color="dodgerblue"), row=i%num_cols + 1, col = i//num_rows + 1)
    fig.add_trace(go.Scatter(y=reconstruction, marker_line_color="coral"), row=i%num_cols + 1, col = i//num_rows + 1)

fig.update_layout(height=1000)
fig.update_xaxes(title="sample number")
fig.update_yaxes(title="amplitude")
fig.show()

### Latent space exploration

In [43]:
# Try some latent space exploration

with torch.no_grad():
    model.eval()
    for i, (signals, _, _) in enumerate(test_dataloader):
        signals = torch.unsqueeze(signals.to(device), 1).float()
        # fft = torch.abs(torch.fft.fft(signals))
        # signals = torch.cat([signals, fft], dim=1)
        # labels = labels.type(torch.LongTensor)

        latent_position = model.encode(signals)
        latent_position = latent_position.detach().cpu().numpy()
        signals_np = signals.detach().cpu().numpy()

        print(latent_position.shape)

        break

index = 3
latent_positions = np.zeros((10, *latent_position.shape), dtype=np.float32)
for i in range(10):
    latent_positions[i, :, :] += latent_position
    latent_positions[i, :, index] = i * 4 - 2

signals = []

with torch.no_grad():
    model.eval()
    for l in latent_positions:
        latent = torch.from_numpy(l[:, :60]).to(device)
        signal = model.decode(latent)
        signals.append(signal.detach().cpu().numpy())

(32, 120)


In [49]:
signals = np.array(signals)
print(signals.shape)

plt.plot(signals[:, 1, 0, :].T)
plt.show()

(10, 32, 1, 2048)


### Find the reconstruction error for noisy and clean samples

In [27]:
loss_func = lambda truth, pred: torch.mean((truth - pred) ** 2, dim=(1,2))

with torch.no_grad():
    r_err = []
    inds = []

    model.eval()
    for i, (signals, ci, ind) in enumerate(test_dataloader):
        signals = torch.unsqueeze(signals.to(device), 1).float()
        # fft = torch.abs(torch.fft.fft(signals))
        # signals = torch.cat([signals, fft], dim=1)
        # labels = labels.type(torch.LongTensor)

        output = model(signals)[0]
        signals_np =  signals

        loss = loss_func(output, signals).detach().cpu().numpy()

        for j, l in zip(ind, loss):
            r_err.append(l)
            inds.append(int(j))


    test_dataset["r_err"] = pd.Series(data=r_err, index=inds)

In [28]:
test_dataset.head()

index  ptID   age         ptDiag     ptDiagRev1          ptDiagRev2  \
0    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   
1    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   
2    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   
3    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   
4    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   

           ptDiagRev3  cardRev            measDiag        measDiagRev1  ...  \
0  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   
1  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   
2  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   
3  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   
4  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   

  perhapsAF  measID                                               data  \
0         0     591  [-0.49644204545732973, -0.6246603189506869, -0...   
1         0     591  [0.6110765438273132, 0.6934087028050593, 0.796...   
2         0     591  [4.487455908826463, 5.457356318373902, 6.04539...   
3         0     591  [-0.19036774215761504, -0.13728679542462185, -...   
4         0     591  [-0.2725175881175217, -0.3385749643142289, -0....   

                    file_path class_index  length  rec_ind  rec_pos  \
0  ECGs/000000/saferF2_000591           0    9120      590        0   
1  ECGs/000000/saferF2_000591           0    9120      590        1   
2  ECGs/000000/saferF2_000591           0    9120      590        2   
3  ECGs/000000/saferF2_000591           0    9120      590        3   
4  ECGs/000000/saferF2_000591           0    9120      590        4   

                                      reconstruction     r_err  
0  [-0.21686557, -0.24343641, -0.26114714, -0.271...  0.187477  
1  [0.69952154, 0.739674, 0.76162183, 0.7954289, ...  0.110675  
2  [2.0057967, 2.6896198, 3.3551307, 3.9521482, 4...  0.134242  
3  [0.0681746, 0.07208401, 0.093462884, 0.1240752...  0.116584  
4  [-0.10716759, -0.13234104, -0.15518299, -0.175...  0.095975  

[5 rows x 43 columns]

In [29]:
test_whole_ecgs_rec_err = test_dataset.groupby("rec_ind").agg({"r_err": "mean", "measDiag": lambda x: x.iloc[0]})
test_whole_ecgs_rec_err["measDiag"].value_counts()

DiagEnum.Undecided                 8399
DiagEnum.NoAF                       412
DiagEnum.PoorQuality                164
DiagEnum.AF                           8
DiagEnum.CannotExcludePathology       2
Name: measDiag, dtype: int64

In [123]:
test_whole_ecgs_rec_err.to_pickle("TrainedModels/Autoecoder_small_dataset.pk")

In [30]:
test_not_undecided = test_whole_ecgs_rec_err[test_whole_ecgs_rec_err["measDiag"] != DiagEnum.Undecided]

fig = plt.figure(figsize=(6, 4), dpi=300)
plt.scatter(test_not_undecided["measDiag"].map(lambda x: x.value), test_not_undecided["r_err"], marker='+')
plt.xticks([e.value for e in pd.unique(test_not_undecided["measDiag"])], [e.name for e in pd.unique(test_not_undecided["measDiag"])])
plt.ylabel("Reconstruction error")
plt.xlabel("Measurement diagnosis")
plt.tight_layout()
plt.show()

# plt.savefig("TMRFigures/cvae_reconst_err_large_dataset.png")

# What, it constructs the noisy samples better?

In [31]:
test_not_undecided = test_whole_ecgs_rec_err # [test_whole_ecgs_rec_err["measDiag"] != DiagEnum.Undecided]
test_not_undecided_2 = pd.read_pickle("TrainedModels/Autoecoder_large_dataset.pk")

fig = plt.figure(figsize=(6, 4), dpi=300)

enum_order = [DiagEnum.NoAF, DiagEnum.AF, DiagEnum.CannotExcludePathology, DiagEnum.PoorQuality]
data = [test_not_undecided[test_not_undecided["measDiag"] == e]["r_err"] for e in enum_order]

print(test_not_undecided_2["measDiag"].value_counts())
data_2 = [test_not_undecided_2[test_not_undecided_2["measDiag"] == e]["r_err"] for e in enum_order]

plt.violinplot(data)    # quantiles=[[0.25, 0.75]]*4, showmedians=True)
plt.violinplot(data_2)
plt.xticks([1, 2, 3, 4], [e.name for e in enum_order])
plt.ylabel("Reconstruction error")
plt.xlabel("Measurement diagnosis")
plt.tight_layout()
plt.show()

# plt.savefig("TMRFigures/cvae_reconst_err_small_dataset.png")

DiagEnum.Undecided                 4514
DiagEnum.NoAF                       120
DiagEnum.PoorQuality                108
DiagEnum.CannotExcludePathology       1
Name: measDiag, dtype: int64


ValueError: zero-size array to reduction operation minimum which has no identity

### Sample cross validation code for SAFER (not yet applied to anything)

In [132]:
# Cross Validation dataset construction for SAFER data
# Split train and test data according to each patient
feas2_pt_data["noLQrecs"] = feas2_pt_data["noRecs"] - feas2_pt_data["noHQrecs"]

num_folds = 5
test_pt_folds = [[] for _ in range(num_folds)]

sorted_pts = feas2_pt_data.sort_values("noLQrecs", axis=0)
group_num = 0

# Go around the folds and assign patients to each
for _, pt in sorted_pts.iterrows():
    test_pt_folds[group_num].append(pt)
    group_num = (group_num + 1) % num_folds

test_pt_folds = [pd.DataFrame(fold) for fold in test_pt_folds]
train_pt_folds = [feas2_pt_data[~feas2_pt_data["ptID"].isin(fold["ptID"])] for fold in test_pt_folds]

for i, fold in enumerate(test_pt_folds):
    print(f"Fold {i}")
    print(fold[["noLQrecs", "noHQrecs"]].sum(axis=0))

Fold 0
noLQrecs     118.0
noHQrecs    4461.0
dtype: float64
Fold 1
noLQrecs     120.0
noHQrecs    4643.0
dtype: float64
Fold 2
noLQrecs     131.0
noHQrecs    4570.0
dtype: float64
Fold 3
noLQrecs     102.0
noHQrecs    4500.0
dtype: float64
Fold 4
noLQrecs     109.0
noHQrecs    4505.0
dtype: float64


### Classification from the latent space

In [32]:
from sklearn.svm import SVC

classifier = SVC(C=1)

train_dataset["latent_encoding"] = None

with torch.no_grad():
    model.eval()
    for i, (signals, _, ind) in enumerate(train_dataloader):
        signals = torch.unsqueeze(signals.to(device), 1).float()
        # fft = torch.abs(torch.fft.fft(signals))
        # signals = torch.cat([signals, fft], dim=1)
        # labels = labels.type(torch.LongTensor)

        latent_position = model.encode(signals)
        latent_position = latent_position.detach().cpu().numpy()
        signals_np = signals.detach().cpu().numpy()

        for i, l in zip(ind, latent_position):
            train_dataset["latent_encoding"].loc[int(i)] = l

svc_train_df = train_dataset.dropna(subset=["latent_encoding"])

C:\Users\daniel\AppData\Local\Temp\ipykernel_71904\931485503.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_dataset["latent_encoding"].loc[int(i)] = l


#### Visualise the data with scatter plots and T-SNE

In [33]:
latent_list = list(svc_train_df["latent_encoding"].map(lambda x: x[:60].tolist()).values)
latent_df = pd.DataFrame(latent_list, index=svc_train_df.index)
print(latent_df.columns)

latent_ind = 0

for i in range(60):
    plt.figure(figsize=(6, 4), dpi=300)
    for d in [DiagEnum.NoAF, DiagEnum.PoorQuality, DiagEnum.AF, DiagEnum.CannotExcludePathology]:
        plt.scatter(latent_df[svc_train_df["measDiag"] == d][0], latent_df[svc_train_df["measDiag"] == d][i], marker="x", label=d.name)
    plt.legend()
    plt.ylabel(f"latent mean {i}")
    plt.xlabel(f"latent mean 0")
    plt.show()

"""
x_clean = latent_matrix[:, latent_inds[0]]
y_clean = latent_matrix[:, latent_inds[1]]

plt.scatter(x_clean, y_clean, c=train_dataset["class_index"])
plt.show()
"""

RangeIndex(start=0, stop=60, step=1)


KeyboardInterrupt: 

In [34]:
svc_train_df = svc_train_df[svc_train_df["measDiag"] != DiagEnum.Undecided]

In [35]:
from sklearn.manifold import TSNE

latent_matrix = np.array(list(svc_train_df["latent_encoding"].map(lambda x: x[:60].tolist()).values))
latent_classes = svc_train_df["measDiag"].values

print("starting tsne")
tsne = TSNE(n_components=2, learning_rate='auto', init='random', perplexity=30)

X_embedded = tsne.fit_transform(latent_matrix)

for d in [DiagEnum.NoAF, DiagEnum.PoorQuality, DiagEnum.AF, DiagEnum.CannotExcludePathology]:
    plt.scatter(X_embedded[latent_classes == d, 0], X_embedded[latent_classes == d, 1], marker="x", label=d.name)

plt.legend()
plt.show()

starting tsne


#### Group all the segments together

In [36]:
svc_train_df = svc_train_df[svc_train_df["measDiag"] != DiagEnum.Undecided]

def concatenate_means(x):
    mean_series = x.map(lambda x: x[:60])
    return np.concatenate(mean_series.tolist())

full_ecg_train_df = svc_train_df.groupby("rec_ind").agg({"latent_encoding": concatenate_means, "measDiag": lambda x: x.iloc[0], "class_index": lambda x: x.iloc[0]})
full_ecg_train_df.iloc[0]["latent_encoding"].shape

(420,)

In [37]:
latent_matrix = np.array(list(full_ecg_train_df["latent_encoding"].map(lambda x: x.tolist()).values))
latent_classes = full_ecg_train_df["measDiag"].values

print("starting tsne")
tsne = TSNE(n_components=2, learning_rate='auto', init='random', perplexity=30)

X_embedded = tsne.fit_transform(latent_matrix)

for d in [DiagEnum.NoAF, DiagEnum.PoorQuality, DiagEnum.AF, DiagEnum.CannotExcludePathology]:
    plt.scatter(X_embedded[latent_classes == d, 0], X_embedded[latent_classes == d, 1], marker="x", label=d.name)

plt.legend()
plt.show()

starting tsne


In [38]:
svc_train_df["class_index"].value_counts()

0    2478
1    2107
Name: class_index, dtype: int64

In [43]:
reduced_normal_samps = svc_train_df[svc_train_df["class_index"] == 0].sample(frac=0.2)
reduced_train_df = pd.concat([reduced_normal_samps, svc_train_df[svc_train_df["class_index"] == 1]])

train_matrix = np.vstack(reduced_train_df["latent_encoding"].values)
targets =  np.array(reduced_train_df["class_index"].astype(int).values)

print(train_matrix.shape)

classifier = classifier.fit(train_matrix, targets)

(3296, 120)


In [39]:
train_matrix = np.vstack(full_ecg_train_df["latent_encoding"].values)
targets =  np.array(full_ecg_train_df["class_index"].astype(int).values)

print(train_matrix.shape)

classifier = classifier.fit(train_matrix, targets)

(655, 420)


In [40]:
test_dataset["latent_encoding"] = None
inds = []
latents = []

with torch.no_grad():
    model.eval()
    for i, (signals, _,  ind) in enumerate(test_dataloader):
        signals = torch.unsqueeze(signals.to(device), 1).float()
        # fft = torch.abs(torch.fft.fft(signals))
        # signals = torch.cat([signals, fft], dim=1)
        # labels = labels.type(torch.LongTensor)

        latent_position = model.encode(signals)
        latent_position = latent_position.detach().cpu().numpy()

        for i, l in zip(ind, latent_position):
            inds.append(int(i))
            latents.append(l)

test_dataset["latent_encoding"] = pd.Series(data=latents, index=inds)

In [41]:
test_dataset.head()

index  ptID   age         ptDiag     ptDiagRev1          ptDiagRev2  \
0    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   
1    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   
2    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   
3    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   
4    590     8  72.5  DiagEnum.NoAF  DiagEnum.NoAF  DiagEnum.Undecided   

           ptDiagRev3  cardRev            measDiag        measDiagRev1  ...  \
0  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   
1  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   
2  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   
3  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   
4  DiagEnum.Undecided        1  DiagEnum.Undecided  DiagEnum.Undecided  ...   

  measID                                               data  \
0    591  [-0.49644204545732973, -0.6246603189506869, -0...   
1    591  [0.6110765438273132, 0.6934087028050593, 0.796...   
2    591  [4.487455908826463, 5.457356318373902, 6.04539...   
3    591  [-0.19036774215761504, -0.13728679542462185, -...   
4    591  [-0.2725175881175217, -0.3385749643142289, -0....   

                    file_path  class_index length  rec_ind  rec_pos  \
0  ECGs/000000/saferF2_000591            0   9120      590        0   
1  ECGs/000000/saferF2_000591            0   9120      590        1   
2  ECGs/000000/saferF2_000591            0   9120      590        2   
3  ECGs/000000/saferF2_000591            0   9120      590        3   
4  ECGs/000000/saferF2_000591            0   9120      590        4   

                                      reconstruction     r_err  \
0  [-0.21686557, -0.24343641, -0.26114714, -0.271...  0.187477   
1  [0.69952154, 0.739674, 0.76162183, 0.7954289, ...  0.110675   
2  [2.0057967, 2.6896198, 3.3551307, 3.9521482, 4...  0.134242   
3  [0.0681746, 0.07208401, 0.093462884, 0.1240752...  0.116584   
4  [-0.10716759, -0.13234104, -0.15518299, -0.175...  0.095975   

                                     latent_encoding  
0  [-4.0090117, -3.826209, -3.1733475, 0.2200228,...  
1  [-0.8080504, 1.5049365, 0.1818518, -0.01725173...  
2  [0.9529757, 0.31610537, -1.6506605, -2.5034447...  
3  [5.789559, 3.1293926, 2.2372184, 0.5986618, 1....  
4  [-0.15044999, -2.0908425, -1.4669328, -0.18167...  

[5 rows x 44 columns]

In [42]:
full_ecg_test_df = test_dataset.groupby("rec_ind").agg({"latent_encoding": concatenate_means, "measDiag": lambda x: x.iloc[0], "class_index": lambda x: x.iloc[0], "measID": lambda x: x.iloc[0]})
full_ecg_no_undecided_test_df = full_ecg_test_df[full_ecg_test_df["measDiag"] != DiagEnum.Undecided]

test_matrix = np.vstack(full_ecg_no_undecided_test_df["latent_encoding"].values)
targets =  np.array(full_ecg_no_undecided_test_df["class_index"].astype(int).values)
print(test_matrix.shape)

prediction = classifier.predict(test_matrix)

full_ecg_no_undecided_test_df["prediction"] = prediction

(586, 420)


C:\Users\daniel\AppData\Local\Temp\ipykernel_71904\3497999537.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  full_ecg_no_undecided_test_df["prediction"] = prediction


In [43]:
from sklearn.metrics import ConfusionMatrixDisplay, confusion_matrix

conf_mat = confusion_matrix(full_ecg_no_undecided_test_df["class_index"].astype(int), full_ecg_no_undecided_test_df["prediction"].astype(int))
print(conf_mat)

def F1_ind(conf_mat, ind):
    return (2 * conf_mat[ind, ind])/(np.sum(conf_mat[ind]) + np.sum(conf_mat[:, ind]))

print(f"Sensitivity: {conf_mat[1, 1]/np.sum(conf_mat[1])}")
print(f"Specificity: {conf_mat[0, 0]/np.sum(conf_mat[0])}")

print(f"Normal F1: {F1_ind(conf_mat, 0)}")
print(f"Noisy F1: {F1_ind(conf_mat, 1)}")

[[280 142]
 [ 41 123]]
Sensitivity: 0.75
Specificity: 0.6635071090047393
Normal F1: 0.7537012113055181
Noisy F1: 0.5734265734265734


In [50]:
false_positives = full_ecg_no_undecided_test_df[(full_ecg_no_undecided_test_df["class_index"] == 0) & (full_ecg_no_undecided_test_df["prediction"] == 1)]

In [51]:
for _, ecg in feas2_ecg_data[feas2_ecg_data["measID"].isin(false_positives["measID"])]["data"].iteritems():
    plot_ecg_and_reconstruction(ecg, ecg)
    plt.show()

C:\Users\daniel\AppData\Local\Temp\ipykernel_156864\2192664923.py:1: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for _, ecg in feas2_ecg_data[feas2_ecg_data["measID"].isin(false_positives["measID"])]["data"].iteritems():


KeyboardInterrupt: 

### Interpolate between a noisy and clean ECG!

In [171]:
# noisy 441 # clean 315

noisy_latent = test_dataset.loc[441]["latent_encoding"][:60]
clean_latent = test_dataset.loc[315]["latent_encoding"][:60]

latent_sequence = np.linspace(noisy_latent, clean_latent, 32)
latent_sequence = torch.from_numpy(latent_sequence).to(device)

ecgs = model.decode(latent_sequence).detach().cpu().numpy()
print("plotting")

for ecg in np.flip(ecgs[:, 0, :], axis=0):
    plt.plot(ecg)
    plt.show()

plotting
